# Data Science Capstone Project Notebook



In [ ]:
In this project, we will find the best place to have an Italian restaurant. We will 

### Installing packages that we would be using later on in this project

In [1]:
!conda install -c conda-forge geopy --yes
!conda install -c conda-forge folium=0.5.0 --yes

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

### Importing libraries and dependencies that we would need to use throughout this project

In [124]:
import pandas as pd

import numpy as np
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.options.mode.chained_assignment = None

import json # library to handle JSON files
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geopy.distance

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

We first need to get the breakdrown of the Colombo district by postal code.
This can be obtained by scraping the Wikipedia page below.
https://en.wikipedia.org/wiki/Postal_codes_in_Sri_Lanka

In [69]:
scraped_data=pd.read_html("https://en.wikipedia.org/wiki/Postal_codes_in_Sri_Lanka")
table=scraped_data[1]
table.head()

Province      District      City3666  Post Code
0        Eastern        Ampara        Ampara      32000
1        Eastern    Kattankudy    Kattankudy      30100
2        Eastern    Batticaloa    Batticaloa      30000
3  North Central  Anuradhapura  Anuradhapura      50000
4            Uva       Badulla       Badulla      90001

### Cleaning the Data

In [77]:
#Filter to get only the areas in the Colombo District
df_cmb=table[table.District=='Colombo']


#Remove redundant columns
df_cmb=df_cmb[['City3666','Post Code']]
df_cmb.rename(columns={'City3666':'City','Post Code':'Postal Code'},inplace=True)
df_cmb.set_index('Postal Code',inplace=True)
df_cmb.reset_index(inplace=True)
df_cmb['Postal Code'] = df_cmb['Postal Code'].apply('{0:0>5}'.format)

df_cmb

Postal Code                 City
0        10120         Battaramulla
1        00400        Bambalapitiya
2        00600           Wellawatte
3        00300             Colpetty
4        00500          Narahenpita
5        00800              Borella
6        00700     Cinnamon Gardens
7        00900           Dematagoda
8        00100                 Fort
9        01200            Hultsdorf
10       01300             Kotahena
11       01000             Maradana
12       01400            Grandpass
13       01500               Mutwal
14       01100               Pettah
15       00200         Slave Island
16       10100  Sri Jayawardenepura
17       10107           Rajagiriya
18       10350             Dehiwala
19       10600            Kolonnawa
20       10280           Maharagama
21       10400             Moratuwa
22       10370        Mount Lavinia

In [104]:
#Manual edits
df_cmb['City'].replace(to_replace='Colpetty', value='Kollupitiya',inplace=True)
df_cmb['City'].replace(to_replace='Hultsdorf', value='Hulftsdorp',inplace=True)
df_cmb

Postal Code                 City  Latitude  Longitude
0        10120         Battaramulla  6.902181  79.919578
1        00400        Bambalapitiya  6.901825  79.854683
2        00600           Wellawatte  6.874128  79.859332
3        00300          Kollupitiya  6.921812  79.865561
4        00500          Narahenpita  6.905727  79.882130
5        00800              Borella  6.917932  79.880256
6        00700     Cinnamon Gardens  6.910335  79.866994
7        00900           Dematagoda  6.936130  79.880049
8        00100                 Fort  6.946338  79.843968
9        01200           Hulftsdorp  0.000000   0.000000
10       01300             Kotahena  0.000000   0.000000
11       01000             Maradana  0.000000   0.000000
12       01400            Grandpass  0.000000   0.000000
13       01500               Mutwal  0.000000   0.000000
14       01100               Pettah  0.000000   0.000000
15       00200         Slave Island  0.000000   0.000000
16       10100  Sri Jayawardenepura  0.000000   0.000000
17       10107           Rajagiriya  0.000000   0.000000
18       10350             Dehiwala  0.000000   0.000000
19       10600            Kolonnawa  0.000000   0.000000
20       10280           Maharagama  0.000000   0.000000
21       10400             Moratuwa  0.000000   0.000000
22       10370        Mount Lavinia  0.000000   0.000000

In [105]:
print("The dimensions of the dataframe are",df_cmb.shape)

The dimensions of the dataframe are (23, 4)


### Adding the location data

In [107]:
df_cmb['Latitude']=0.0
df_cmb['Longitude']=0.0

geolocator = Nominatim(user_agent="cmb_explorer")

for i in df_cmb.index:
    address=df_cmb.at[i,'City']+', Colombo'
    print(address)
    
    location=None
    while(location is None):
        location = geolocator.geocode(address)
        
    latitude = location.latitude
    longitude = location.longitude
    df_cmb.at[i,'Latitude']=latitude
    df_cmb.at[i,'Longitude']=longitude

Battaramulla, Colombo
Bambalapitiya, Colombo
Wellawatte, Colombo
Kollupitiya, Colombo
Narahenpita, Colombo
Borella, Colombo
Cinnamon Gardens, Colombo
Dematagoda, Colombo
Fort, Colombo
Hulftsdorp, Colombo
Kotahena, Colombo
Maradana, Colombo
Grandpass, Colombo
Mutwal, Colombo
Pettah, Colombo
Slave Island, Colombo
Sri Jayawardenepura, Colombo
Rajagiriya, Colombo
Dehiwala, Colombo
Kolonnawa, Colombo
Maharagama, Colombo
Moratuwa, Colombo
Mount Lavinia, Colombo


In [108]:
#Displaying the dataframe with coordinates added.
display(df_cmb)

Postal Code                 City  Latitude  Longitude
0        10120         Battaramulla  6.902181  79.919578
1        00400        Bambalapitiya  6.901825  79.854683
2        00600           Wellawatte  6.874128  79.859332
3        00300          Kollupitiya  6.921812  79.865561
4        00500          Narahenpita  6.905727  79.882130
5        00800              Borella  6.917932  79.880256
6        00700     Cinnamon Gardens  6.910335  79.866994
7        00900           Dematagoda  6.936130  79.880049
8        00100                 Fort  6.946338  79.843968
9        01200           Hulftsdorp  6.935853  79.860260
10       01300             Kotahena  6.948985  79.858923
11       01000             Maradana  6.926799  79.863879
12       01400            Grandpass  6.943993  79.873717
13       01500               Mutwal  6.962534  79.864048
14       01100               Pettah  6.934129  79.852892
15       00200         Slave Island  6.924657  79.850273
16       10100  Sri Jayawardenepura  6.886693  79.918738
17       10107           Rajagiriya  6.909504  79.896218
18       10350             Dehiwala  6.851279  79.865977
19       10600            Kolonnawa  6.932625  79.890314
20       10280           Maharagama  6.847278  79.926608
21       10400             Moratuwa  6.774682  79.882610
22       10370        Mount Lavinia  6.832936  79.867410

## Creating a map of Colombo with all the neighborhood centres marked

In [110]:
central_loc = [df_cmb.Latitude.mean(),df_cmb.Longitude.mean()]
central_loc

[6.905580743478263, 79.87497467983943]

In [122]:
# create map of Colombo using latitude and longitude values
map_cmb = folium.Map(location=[central_loc[0], central_loc[1]], zoom_start=11)

# add markers to map
for lat, lng, label in zip(df_cmb['Latitude'], df_cmb['Longitude'], df_cmb['City']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_cmb)  
    
map_cmb

## Distance between neighborhood centres

In [184]:
dist=np.zeros((df_cmb.index.size, df_cmb.index.size),dtype=float)

for p in df_cmb.index:
    for q in df_cmb.index:
        coord1=(df_cmb.at[p,'Latitude'],df_cmb.at[p,'Longitude'])
        coord2=(df_cmb.at[q,'Latitude'],df_cmb.at[q,'Longitude'])
        temp=geopy.distance.distance(coord1,coord2).km
        dist[p,q]=temp

min_dist=min(dist[np.nonzero(dist)])
print("The minimum distance between two neighborhood centres is {:.2f} km".format(min(dist[np.nonzero(dist)])))
print("The maximum distance between two neighborhood centres is {:.2f} km".format(max(dist[np.nonzero(dist)])))


The minimum distance between two neighborhood centres is 0.58 km
The maximum distance between two neighborhood centres is 20.88 km


In [172]:
#Displaying distance between neighbourhood centres as a dataframe.
df_dist=pd.DataFrame(data=dist,
                   index=df_cmb['City'],
                 columns=df_cmb['City'])

del df_dist.index.name
del df_dist.columns.name
display(df_dist)

Battaramulla  Bambalapitiya  Wellawatte  Kollupitiya  \
Battaramulla             0.000000       7.172127    7.345687     6.352228   
Bambalapitiya            7.172127       0.000000    3.105831     2.516146   
Wellawatte               7.345687       3.105831    0.000000     5.318158   
Kollupitiya              6.352228       2.516146    5.318158     0.000000   
Narahenpita              4.157186       3.063867    4.308110     2.552958   
Borella                  4.681824       3.340729    5.367972     1.679730   
Cinnamon Gardens         5.880936       1.654349    4.092720     1.279101   
Dematagoda               5.760166       4.717116    7.228974     2.251818   
Fort                     9.678181       5.063124    8.164260     3.612588   
Hulftsdorp               7.539251       3.813312    6.826975     1.659605   
Kotahena                 8.468938       5.236385    8.278536     3.093234   
Maradana                 6.730701       2.942909    5.846519     0.581933   
Grandpass                6.860673       5.115817    7.888257     2.613333   
Mutwal                   9.066788       6.793111    9.790726     4.506529   
Pettah                   8.172929       3.577994    6.673614     1.953383   
Slave Island             8.052434       2.571599    5.677009     1.718514   
Sri Jayawardenepura      1.715373       7.274450    6.711132     7.044420   
Rajagiriya               2.705731       4.668171    5.650158     3.651236   
Dehiwala                 8.172196       5.727650    2.631510     7.800497   
Kolonnawa                4.668479       5.206552    7.319515     2.985505   
Maharagama               6.121210       9.979164    8.006816    10.652038   
Moratuwa                14.680245      14.395606   11.294709    16.379904   
Mount Lavinia            9.585784       7.747265    4.642131     9.830995   

                     Narahenpita    Borella  Cinnamon Gardens  Dematagoda  \
Battaramulla            4.157186   4.681824          5.880936    5.760166   
Bambalapitiya           3.063867   3.340729          1.654349    4.717116   
Wellawatte              4.308110   5.367972          4.092720    7.228974   
Kollupitiya             2.552958   1.679730          1.279101    2.251818   
Narahenpita             0.000000   1.365648          1.748671    3.370195   
Borella                 1.365648   0.000000          1.689370    2.012616   
Cinnamon Gardens        1.748671   1.689370          0.000000    3.196740   
Dematagoda              3.370195   2.012616          3.196740    0.000000   
Fort                    6.160954   5.094128          4.725271    4.143990   
Hulftsdorp              4.116028   2.968308          2.918515    2.187061   
Kotahena                5.428011   4.165421          4.366325    2.733357   
Maradana                3.082015   2.058383          1.852974    2.063487   
Grandpass               4.332859   2.971294          3.795665    1.116186   
Mutwal                  6.592490   5.247636          5.781856    3.413656   
Pettah                  4.506341   3.514769          3.058293    3.009314   
Slave Island            4.096051   3.395908          2.433784    3.526678   
Sri Jayawardenepura     4.560739   5.479369          6.288056    6.940716   
Rajagiriya              1.612020   1.995133          3.230986    3.444328   
Dehiwala                6.280501   7.538318          6.532072    9.511770   
Kolonnawa               3.109229   1.968735          3.566309    1.198815   
Maharagama              8.120790   9.343350          9.593817   11.091974   
Moratuwa               14.492306  15.844200         15.100857   17.856793   
Mount Lavinia           8.212681   9.506401          8.559737   11.497440   

                          Fort  Hulftsdorp   Kotahena   Maradana  Grandpass  \
Battaramulla          9.678181    7.539251   8.468938   6.730701   6.860673   
Bambalapitiya         5.063124    3.813312   5.236385   2.942909   5.115817   
Wellawatte            8.164260    6.826975   8.278536   5.846519   7.888257   
Kollupi

From the above, we can see that there are varying distances between the neighbourhood centres.

# Getting venue data using Foursquare API

### General Function to obtain nearby venues using Foursquare API

#### Credit: Alex Aklson and Polong Lin

In [186]:
def getNearbyVenues(names, latitudes, longitudes, radius, LIMIT):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
        
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Using the above function, we can call the Foursquares API to obtain the venues near each of the neighbourhood centres

#### Define Foursquare Credentials and Version

In [188]:
# The code was removed by Watson Studio for sharing.

### We call the function define above to obtain the nearby venues for the neighborhoods in Colombo

We use a search radius of 1 km for searching for the venues, as well as a maximum limit of 100 venues per neighbourhood.

In [197]:
cmb_venues = getNearbyVenues(names=df_cmb['City'],
                                   latitudes=df_cmb['Latitude'],
                                   longitudes=df_cmb['Longitude'],
                                    radius=1000,
                                 LIMIT = 100
                                  )

Battaramulla
Bambalapitiya
Wellawatte
Kollupitiya
Narahenpita
Borella
Cinnamon Gardens
Dematagoda
Fort
Hulftsdorp
Kotahena
Maradana
Grandpass
Mutwal
Pettah
Slave Island
Sri Jayawardenepura
Rajagiriya
Dehiwala
Kolonnawa
Maharagama
Moratuwa
Mount Lavinia


In [190]:
cmb_venues

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           Battaramulla               6.902181               79.919578   
1           Battaramulla               6.902181               79.919578   
2           Battaramulla               6.902181               79.919578   
3           Battaramulla               6.902181               79.919578   
4           Battaramulla               6.902181               79.919578   
5           Battaramulla               6.902181               79.919578   
6           Battaramulla               6.902181               79.919578   
7           Battaramulla               6.902181               79.919578   
8           Battaramulla               6.902181               79.919578   
9           Battaramulla               6.902181               79.919578   
10          Battaramulla               6.902181               79.919578   
11         Bambalapitiya               6.901825               79.854683   
12         Bambalapitiya               6.901825               79.854683   
13         Bambalapitiya               6.901825               79.854683   
14         Bambalapitiya               6.901825               79.854683   
15         Bambalapitiya               6.901825               79.854683   
16         Bambalapitiya               6.901825               79.854683   
17         Bambalapitiya               6.901825               79.854683   
18         Bambalapitiya               6.901825               79.854683   
19         Bambalapitiya               6.901825               79.854683   
20         Bambalapitiya               6.901825               79.854683   
21         Bambalapitiya               6.901825               79.854683   
22         Bambalapitiya               6.901825               79.854683   
23         Bambalapitiya               6.901825               79.854683   
24         Bambalapitiya               6.901825               79.854683   
25         Bambalapitiya               6.901825               79.854683   
26         Bambalapitiya               6.901825               79.854683   
27         Bambalapitiya               6.901825               79.854683   
28         Bambalapitiya               6.901825               79.854683   
29         Bambalapitiya               6.901825               79.854683   
30         Bambalapitiya               6.901825               79.854683   
31         Bambalapitiya               6.901825               79.854683   
32         Bambalapitiya               6.901825               79.854683   
33         Bambalapitiya               6.901825               79.854683   
34         Bambalapitiya               6.901825               79.854683   
35         Bambalapitiya               6.901825               79.854683   
36         Bambalapitiya               6.901825               79.854683   
37         Bambalapitiya               6.901825               79.854683   
38         Bambalapitiya               6.901825               79.854683   
39         Bambalapitiya               6.901825               79.854683   
40         Bambalapitiya               6.901825               79.854683   
41         Bambalapitiya               6.901825               79.854683   
42         Bambalapitiya               6.901825               79.854683   
43         Bambalapitiya               6.901825               79.854683   
44         Bambalapitiya               6.901825               79.854683   
45         Bambalapitiya               6.901825               79.854683   
46         Bambalapitiya               6.901825               79.854683   
47         Bambalapitiya               6.901825               79.854683   
48         Bambalapitiya               6.901825               79.854683   
49         Bambalapitiya               6.901825               79.854683   
50         Bambalapitiya               6.901825               79.854683   
51         Bambalapitiya               6.901825               79.854683   
52         Bambalapitiya             

In [198]:
cmb_venues.shape

(928, 7)

#### There are 928 venues that have popped up. We need to filter this in order to isolate the existing restaurants.

#### We now inspect the list of unique venue categories that are present in the dataframe we just obtained

In [204]:
cmb_venues['Venue Category'].unique()

array(['Department Store', 'Food', 'Lake', 'Fast Food Restaurant',
       'Cocktail Bar', 'Bakery', 'Italian Restaurant',
       'Japanese Restaurant', 'Asian Restaurant', 'Chinese Restaurant',
       'Coffee Shop', 'Food Court', 'Clothing Store', 'Restaurant',
       'Food & Drink Shop', 'Garden', 'Outdoors & Recreation',
       'Indian Restaurant', 'Dessert Shop', "Men's Store", 'Hotel',
       'Café', 'IT Services', 'Thai Restaurant', 'Cupcake Shop', 'Hostel',
       'Lounge', 'Boutique', 'Seafood Restaurant',
       'Middle Eastern Restaurant', 'Art Gallery', 'Optical Shop',
       'Paper / Office Supplies Store', 'Casino', 'Jewelry Store',
       'Bed & Breakfast', 'Bubble Tea Shop', 'Sporting Goods Shop',
       'Office', 'Multiplex', 'Gastropub', 'Bookstore',
       'Sri Lankan Restaurant', 'Sandwich Place', 'Shopping Mall',
       'Grocery Store', 'Gift Shop', 'Lingerie Store', 'Theater',
       'Pizza Place', 'Playground', 'Juice Bar', 'Electronics Store',
       'American Res

#### From the above categories, we need to extract the data for the restaurants and other eating establishments.

#### For this, we first inspect the above list of unique venue categories to find keywords with which we could filter the list.

In [255]:
#We use the keywords to extract only the entries for restaurants from the dataframe.

keywords=['Restaurant','Snack','Noodle','Food','Dessert','Café','Diner','Buffet','Bistro','Sandwich','Pizza','Gastropub','Breakfast','BBQ','Burger']
cmb_res=cmb_venues[cmb_venues['Venue Category'].str.contains('|'.join(keywords))]
cmb_res


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
1           Battaramulla               6.902181               79.919578   
3           Battaramulla               6.902181               79.919578   
5           Battaramulla               6.902181               79.919578   
7           Battaramulla               6.902181               79.919578   
8           Battaramulla               6.902181               79.919578   
9           Battaramulla               6.902181               79.919578   
11          Battaramulla               6.902181               79.919578   
13          Battaramulla               6.902181               79.919578   
15          Battaramulla               6.902181               79.919578   
17          Battaramulla               6.902181               79.919578   
18          Battaramulla               6.902181               79.919578   
21          Battaramulla               6.902181               79.919578   
22          Battaramulla               6.902181               79.919578   
23          Battaramulla               6.902181               79.919578   
24          Battaramulla               6.902181               79.919578   
27         Bambalapitiya               6.901825               79.854683   
29         Bambalapitiya               6.901825               79.854683   
31         Bambalapitiya               6.901825               79.854683   
33         Bambalapitiya               6.901825               79.854683   
34         Bambalapitiya               6.901825               79.854683   
35         Bambalapitiya               6.901825               79.854683   
36         Bambalapitiya               6.901825               79.854683   
44         Bambalapitiya               6.901825               79.854683   
45         Bambalapitiya               6.901825               79.854683   
47         Bambalapitiya               6.901825               79.854683   
54         Bambalapitiya               6.901825               79.854683   
57         Bambalapitiya               6.901825               79.854683   
58         Bambalapitiya               6.901825               79.854683   
59         Bambalapitiya               6.901825               79.854683   
60         Bambalapitiya               6.901825               79.854683   
61         Bambalapitiya               6.901825               79.854683   
62         Bambalapitiya               6.901825               79.854683   
69         Bambalapitiya               6.901825               79.854683   
71         Bambalapitiya               6.901825               79.854683   
72         Bambalapitiya               6.901825               79.854683   
77         Bambalapitiya               6.901825               79.854683   
81         Bambalapitiya               6.901825               79.854683   
84         Bambalapitiya               6.901825               79.854683   
85         Bambalapitiya               6.901825               79.854683   
86         Bambalapitiya               6.901825               79.854683   
87         Bambalapitiya               6.901825               79.854683   
89         Bambalapitiya               6.901825               79.854683   
90         Bambalapitiya               6.901825               79.854683   
92         Bambalapitiya               6.901825               79.854683   
93         Bambalapitiya               6.901825               79.854683   
100        Bambalapitiya               6.901825               79.854683   
101        Bambalapitiya               6.901825               79.854683   
102        Bambalapitiya               6.901825               79.854683   
105        Bambalapitiya               6.901825               79.854683   
110        Bambalapitiya               6.901825               79.854683   
111        Bambalapitiya               6.901825               79.854683   
112        Bambalapitiya               6.901825               79.854683   
118        Bambalapitiya             

Now that we have isolated the restaurants, its time to move on to the modelling.

In order to analyze the best place for a restaurant, we will use K-means clustering to cluster the neighborhoods according to restaurant density.

Since we assume that our restaurant would be located at the centre of the neighbourhood, the further another restaurant is from the centre, its effect on our restaurant would be presumably lower.

Therefore we apply a linear weighting factor to each restaurant venue, based on the distance from the neighborhood centre.


In [256]:
cmb_res
cmb_res['Weighting Factor']=0
cmb_res.reset_index(drop=True)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           Battaramulla               6.902181               79.919578   
1           Battaramulla               6.902181               79.919578   
2           Battaramulla               6.902181               79.919578   
3           Battaramulla               6.902181               79.919578   
4           Battaramulla               6.902181               79.919578   
5           Battaramulla               6.902181               79.919578   
6           Battaramulla               6.902181               79.919578   
7           Battaramulla               6.902181               79.919578   
8           Battaramulla               6.902181               79.919578   
9           Battaramulla               6.902181               79.919578   
10          Battaramulla               6.902181               79.919578   
11          Battaramulla               6.902181               79.919578   
12          Battaramulla               6.902181               79.919578   
13          Battaramulla               6.902181               79.919578   
14          Battaramulla               6.902181               79.919578   
15         Bambalapitiya               6.901825               79.854683   
16         Bambalapitiya               6.901825               79.854683   
17         Bambalapitiya               6.901825               79.854683   
18         Bambalapitiya               6.901825               79.854683   
19         Bambalapitiya               6.901825               79.854683   
20         Bambalapitiya               6.901825               79.854683   
21         Bambalapitiya               6.901825               79.854683   
22         Bambalapitiya               6.901825               79.854683   
23         Bambalapitiya               6.901825               79.854683   
24         Bambalapitiya               6.901825               79.854683   
25         Bambalapitiya               6.901825               79.854683   
26         Bambalapitiya               6.901825               79.854683   
27         Bambalapitiya               6.901825               79.854683   
28         Bambalapitiya               6.901825               79.854683   
29         Bambalapitiya               6.901825               79.854683   
30         Bambalapitiya               6.901825               79.854683   
31         Bambalapitiya               6.901825               79.854683   
32         Bambalapitiya               6.901825               79.854683   
33         Bambalapitiya               6.901825               79.854683   
34         Bambalapitiya               6.901825               79.854683   
35         Bambalapitiya               6.901825               79.854683   
36         Bambalapitiya               6.901825               79.854683   
37         Bambalapitiya               6.901825               79.854683   
38         Bambalapitiya               6.901825               79.854683   
39         Bambalapitiya               6.901825               79.854683   
40         Bambalapitiya               6.901825               79.854683   
41         Bambalapitiya               6.901825               79.854683   
42         Bambalapitiya               6.901825               79.854683   
43         Bambalapitiya               6.901825               79.854683   
44         Bambalapitiya               6.901825               79.854683   
45         Bambalapitiya               6.901825               79.854683   
46         Bambalapitiya               6.901825               79.854683   
47         Bambalapitiya               6.901825               79.854683   
48         Bambalapitiya               6.901825               79.854683   
49         Bambalapitiya               6.901825               79.854683   
50         Bambalapitiya               6.901825               79.854683   
51         Bambalapitiya               6.901825               79.854683   
52         Bambalapitiya             

In [268]:
cmb_res['Weighting Factor']=0.0

for i in cmb_res.index:
    coord1=(cmb_res.at[i,'Neighborhood Latitude'],cmb_res.at[i,'Neighborhood Longitude'])
    coord2=(cmb_res.at[i,'Venue Latitude'],cmb_res.at[i,'Venue Longitude'])
    temp=geopy.distance.distance(coord1,coord2).km
    cmb_res.at[i,'Weighting Factor']=1/temp
    #print(temp)
    
cmb_res

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
1           Battaramulla               6.902181               79.919578   
3           Battaramulla               6.902181               79.919578   
5           Battaramulla               6.902181               79.919578   
7           Battaramulla               6.902181               79.919578   
8           Battaramulla               6.902181               79.919578   
9           Battaramulla               6.902181               79.919578   
11          Battaramulla               6.902181               79.919578   
13          Battaramulla               6.902181               79.919578   
15          Battaramulla               6.902181               79.919578   
17          Battaramulla               6.902181               79.919578   
18          Battaramulla               6.902181               79.919578   
21          Battaramulla               6.902181               79.919578   
22          Battaramulla               6.902181               79.919578   
23          Battaramulla               6.902181               79.919578   
24          Battaramulla               6.902181               79.919578   
27         Bambalapitiya               6.901825               79.854683   
29         Bambalapitiya               6.901825               79.854683   
31         Bambalapitiya               6.901825               79.854683   
33         Bambalapitiya               6.901825               79.854683   
34         Bambalapitiya               6.901825               79.854683   
35         Bambalapitiya               6.901825               79.854683   
36         Bambalapitiya               6.901825               79.854683   
44         Bambalapitiya               6.901825               79.854683   
45         Bambalapitiya               6.901825               79.854683   
47         Bambalapitiya               6.901825               79.854683   
54         Bambalapitiya               6.901825               79.854683   
57         Bambalapitiya               6.901825               79.854683   
58         Bambalapitiya               6.901825               79.854683   
59         Bambalapitiya               6.901825               79.854683   
60         Bambalapitiya               6.901825               79.854683   
61         Bambalapitiya               6.901825               79.854683   
62         Bambalapitiya               6.901825               79.854683   
69         Bambalapitiya               6.901825               79.854683   
71         Bambalapitiya               6.901825               79.854683   
72         Bambalapitiya               6.901825               79.854683   
77         Bambalapitiya               6.901825               79.854683   
81         Bambalapitiya               6.901825               79.854683   
84         Bambalapitiya               6.901825               79.854683   
85         Bambalapitiya               6.901825               79.854683   
86         Bambalapitiya               6.901825               79.854683   
87         Bambalapitiya               6.901825               79.854683   
89         Bambalapitiya               6.901825               79.854683   
90         Bambalapitiya               6.901825               79.854683   
92         Bambalapitiya               6.901825               79.854683   
93         Bambalapitiya               6.901825               79.854683   
100        Bambalapitiya               6.901825               79.854683   
101        Bambalapitiya               6.901825               79.854683   
102        Bambalapitiya               6.901825               79.854683   
105        Bambalapitiya               6.901825               79.854683   
110        Bambalapitiya               6.901825               79.854683   
111        Bambalapitiya               6.901825               79.854683   
112        Bambalapitiya               6.901825               79.854683   
118        Bambalapitiya             

In [249]:
cmb_res

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
1           Battaramulla               6.902181               79.919578   
3           Battaramulla               6.902181               79.919578   
5           Battaramulla               6.902181               79.919578   
7           Battaramulla               6.902181               79.919578   
8           Battaramulla               6.902181               79.919578   
9           Battaramulla               6.902181               79.919578   
11          Battaramulla               6.902181               79.919578   
13          Battaramulla               6.902181               79.919578   
15          Battaramulla               6.902181               79.919578   
17          Battaramulla               6.902181               79.919578   
18          Battaramulla               6.902181               79.919578   
21          Battaramulla               6.902181               79.919578   
22          Battaramulla               6.902181               79.919578   
23          Battaramulla               6.902181               79.919578   
24          Battaramulla               6.902181               79.919578   
27         Bambalapitiya               6.901825               79.854683   
29         Bambalapitiya               6.901825               79.854683   
31         Bambalapitiya               6.901825               79.854683   
33         Bambalapitiya               6.901825               79.854683   
34         Bambalapitiya               6.901825               79.854683   
35         Bambalapitiya               6.901825               79.854683   
36         Bambalapitiya               6.901825               79.854683   
44         Bambalapitiya               6.901825               79.854683   
45         Bambalapitiya               6.901825               79.854683   
47         Bambalapitiya               6.901825               79.854683   
54         Bambalapitiya               6.901825               79.854683   
57         Bambalapitiya               6.901825               79.854683   
58         Bambalapitiya               6.901825               79.854683   
59         Bambalapitiya               6.901825               79.854683   
60         Bambalapitiya               6.901825               79.854683   
61         Bambalapitiya               6.901825               79.854683   
62         Bambalapitiya               6.901825               79.854683   
69         Bambalapitiya               6.901825               79.854683   
71         Bambalapitiya               6.901825               79.854683   
72         Bambalapitiya               6.901825               79.854683   
77         Bambalapitiya               6.901825               79.854683   
81         Bambalapitiya               6.901825               79.854683   
84         Bambalapitiya               6.901825               79.854683   
85         Bambalapitiya               6.901825               79.854683   
86         Bambalapitiya               6.901825               79.854683   
87         Bambalapitiya               6.901825               79.854683   
89         Bambalapitiya               6.901825               79.854683   
90         Bambalapitiya               6.901825               79.854683   
92         Bambalapitiya               6.901825               79.854683   
93         Bambalapitiya               6.901825               79.854683   
100        Bambalapitiya               6.901825               79.854683   
101        Bambalapitiya               6.901825               79.854683   
102        Bambalapitiya               6.901825               79.854683   
105        Bambalapitiya               6.901825               79.854683   
110        Bambalapitiya               6.901825               79.854683   
111        Bambalapitiya               6.901825               79.854683   
112        Bambalapitiya               6.901825               79.854683   
118        Bambalapitiya             